# [Amicable Numbers](https://projecteuler.net/problem=21)

The sum of the proper divisors of a number is called the [aliquot sum](https://en.wikipedia.org/wiki/Aliquot_sum).

SageMath [provides the `sigma` function](https://doc.sagemath.org/html/en/reference/rings_standard/sage/arith/misc.html#sage.arith.misc.Sigma), which can compute the sum of the divisors of $n$. The aliquot sum is then just `sigma(n) - n`.

If a number is equal to its own aliquot sum, it's called a [perfect number](https://en.wikipedia.org/wiki/Perfect_number), and we exclude those numbers from our total.

In [1]:
aliquot_sum = lambda n: sigma(n) - n

amicables = set()
for a in range(2, 10000):
    if a in amicables:
        continue
        
    b = aliquot_sum(a)
    if a == b:
        continue
    
    if a == aliquot_sum(b):
        amicables.update({a, b})

print(sum(amicables))

31626


Funny enough, there's only five pairs of amicable numbers below 10,000. If you looked up [amicable numbers](https://en.wikipedia.org/wiki/Amicable_numbers), you may have stumbled on all the numbers you need to answer the problem!

## Sum of divisors
Of course, you could implement your own [divisor sum function](https://en.wikipedia.org/wiki/Divisor_function). In [problem 12](https://projecteuler.net/problem=12), we implemented a divisor *counting* function, which is related.

One important property of the divisor sum function $\sigma(n)$ is that it is [multiplicative](https://en.wikipedia.org/wiki/Multiplicative_function). This means that if $a$ and $b$ are [coprime](https://en.wikipedia.org/wiki/Coprime_integers), $\sigma(ab) = \sigma(a)\sigma(b)$. It follows that if $n = 2^{r_1}3^{r_2}5^{r_3}7^{r_4}\cdots$, then
$$\sigma(n) = \sigma(2^{r_1})\sigma(3^{r_2})\sigma(5^{r_3})\sigma(7^{r_4})\cdots$$

Furthermore, for a prime $p$, $\sigma(p^k) = 1 + p + p^2 + \cdots + p^k$. This expression is actually a partial sum of a [geometric series](https://en.wikipedia.org/wiki/Geometric_series), which has a closed formula:
$$1 + p + p^2 + \cdots + p^k = \frac{p^{k+1}-1}{p-1}$$

Putting it all together, we can compute $\sigma(n)$ as
$$\sigma(n) = \frac{2^{r_1+1}-1}{2-1} \cdot \frac{3^{r_2+1}-1}{3-1} \cdot \frac{5^{r_3+1}-1}{5-1} \cdot \frac{7^{r_4+1}-1}{7-1} \cdot \cdots$$

Therefore, if you have the number's factorization (see [problem 3](https://projecteuler.net/problem=3)), you can use it to compute the sum of its divisors.

## Sieving the sums of divisors
Since we need all the sums of divisors up to 10000, instead of factoring each number individually, we could sieve the values of $\sigma$. This is possible because the sum of divisors function is multiplicative.

In [2]:
def sum_of_divisors_sieve(limit):
    dsum = [1 for _ in range(0, limit)]
    
    for n in range(0, limit):
        if n == 0 or n == 1 or dsum[n] != 1:
            yield dsum[n]
            continue
            
        m = 1
        while m * n < limit:
            dsum[m*n] = dsum[m] + m*n
            for k in range(2 * m * n, limit, m * n):
                if k % (m*n^2) != 0:
                    dsum[k] *= dsum[m*n]
                    
            m *= n
        
        yield dsum[n]

Here's a check to make sure the sieve matches the values from SageMath.

In [3]:
s = list(sum_of_divisors_sieve(10000))
assert all(s[n] == sigma(n) for n in range(1, 10000))

## Relevent sequences
* Amicable numbers: [A063990](https://oeis.org/A063990)